In [20]:
from luna_record_provider_new import LunaRecordProvider
from sziszapangma.integration.experiment_manager import ExperimentManager
from sziszapangma.integration.repository.multi_files_experiment_repository import MultiFilesExperimentRepository
from sziszapangma.integration.path_filter import ExtensionPathFilter
from pymongo import MongoClient
from spacy.tokens.doc import Doc
import pandas as pd

In [21]:
luna_directory = '/Users/marcinwatroba/Desktop/LUNA/LUNA.PL'

In [22]:
experiment_repository = MultiFilesExperimentRepository('experiment_data', 'asr_benchmark_luna')

In [23]:
record_provider = LunaRecordProvider(ExtensionPathFilter(
    root_directory=luna_directory,
    extension='wav'
))

In [24]:
record_id = list(record_provider.get_all_records())[0]

In [25]:
experiment_repository.get_property_for_key(record_id, 'pos_metrics_wer')

{'classic_wer': 0.19727891156462585}

In [26]:
pos_alignment_wer = experiment_repository.get_property_for_key(record_id, 'pos_alignment_wer')
gold_transcript_spacy = experiment_repository.get_property_for_key(record_id, 'gold_transcript_spacy')
gold_trnascript_spacy_word_dict = {it['id']: it['word'] for it in gold_transcript_spacy}
asr_spacy = experiment_repository.get_property_for_key(record_id, 'techmo_spacy')
asr_spacy_word_dict = {it['id']: it['word'] for it in asr_spacy}

In [27]:
arr = [
    {
        'step_type': it['step_type'],
        'reference_word_pos': it['step_words']['reference_word']['text'] if 'reference_word' in it['step_words'] else '',
        'reference_word_text': gold_trnascript_spacy_word_dict[it['step_words']['reference_word']['id']] 
        if 'reference_word' in it['step_words'] else '',
        'hypothesis_word_pos': it['step_words']['hypothesis_word']['text'] if 'hypothesis_word' in it['step_words'] else '',
        'hypothesis_word_text': asr_spacy_word_dict[it['step_words']['hypothesis_word']['id']] 
        if 'hypothesis_word' in it['step_words'] else ''

    }
    for it in pos_alignment_wer
]
pd.DataFrame(arr)

step_type reference_word_pos reference_word_text hypothesis_word_pos  \
0    DELETION               PRON                 xxx                       
1     CORRECT               NOUN               dzień                NOUN   
2     CORRECT                ADJ               dobry                 ADJ   
3     CORRECT               NOUN               dzień                NOUN   
4     CORRECT                ADJ               dobry                 ADJ   
..        ...                ...                 ...                 ...   
143  DELETION               NOUN            widzenia                       
144   CORRECT               VERB              proszę                VERB   
145   CORRECT                ADV              bardzo                 ADV   
146  DELETION                ADP                  do                       
147   CORRECT               NOUN            widzenia                NOUN   

    hypothesis_word_text  
0                         
1                  dzień  
2                  dobry  
3                  dzień  
4                  dobry  
..                   ...  
143                       
144               proszę  
145               bardzo  
146                       
147             widzenia  

[148 rows x 5 columns]

In [47]:
def get_gold_transcript_for(record_id: str) -> str:
    gold_trnascript_property = experiment_repository.get_property_for_key(record_id, 'gold_transcript')
    return ' '.join([it['word'] for it in gold_trnascript_property])

def get_asr_transcript_for(record_id: str) -> str:
    gold_trnascript_property = experiment_repository.get_property_for_key(record_id, 'techmo_polish_asr')
    return gold_trnascript_property['full_text']

def get_pos_alignment_df(record_id: str) -> pd.DataFrame:
    pos_alignment_wer = experiment_repository.get_property_for_key(record_id, 'pos_alignment_wer')
    gold_transcript_spacy = experiment_repository.get_property_for_key(record_id, 'gold_transcript_spacy')
    gold_trnascript_spacy_word_dict = {it['id']: it['word'] for it in gold_transcript_spacy}
    asr_spacy = experiment_repository.get_property_for_key(record_id, 'techmo_spacy')
    asr_spacy_word_dict = {it['id']: it['word'] for it in asr_spacy}
    
    arr = [
        {
            'step_type': it['step_type'],
            'reference_word_pos': it['step_words']['reference_word']['text'] if 'reference_word' in it['step_words'] else '',
            'reference_word_text': gold_trnascript_spacy_word_dict[it['step_words']['reference_word']['id']] 
            if 'reference_word' in it['step_words'] else '',
            'hypothesis_word_pos': it['step_words']['hypothesis_word']['text'] if 'hypothesis_word' in it['step_words'] else '',
            'hypothesis_word_text': asr_spacy_word_dict[it['step_words']['hypothesis_word']['id']] 
            if 'hypothesis_word' in it['step_words'] else ''

        }
        for it in pos_alignment_wer
    ]
    return pd.DataFrame(arr)
    
    
def show_report_for(record_id: str):
    print(f'gold transcript: {get_gold_transcript_for(record_id)}')    
    print()
    print(f'asr transcript: {get_asr_transcript_for(record_id)}')
    print()
    print(f"word wer {experiment_repository.get_property_for_key(record_id, 'techmo_polish_classic_wer_metric')}")
    print()
    print(f"pos wer {experiment_repository.get_property_for_key(record_id, 'pos_metrics_wer')}")
    print()
    display(get_pos_alignment_df(record_id))
    print('--------------------------------------------------------------')
    print('--------------------------------------------------------------')
    print('--------------------------------------------------------------')

In [48]:
for it in list(record_provider.get_all_records())[:20]:
    show_report_for(it)

gold transcript: xxx dzień dobry dzień dobry proszę pana mam takie pytanie jestem emerytką i chcę se kupić miesięczny bilet to ile za jakie muszę czy sto procent płacić czy połówkę a nie ma pani jeszcze siedemdziesięciu lat no nie mam proszę pani jeśli jest pani emerytką to na podstawie legitymacji emery~ emeryta i rencisty i dokumentu tożsamości jest ulga czterdzieści osiem procent czterdzieści osiem procent tak a teraz niech pan mi powie jak ja chcę kupić sobie bilet miesięczny na tą eskaemkę to ile ale pani chce tylko na eskaemkę ? na eskaemkę i na tramwaje aha a będzie pani jeździła eskaemką dokąd ? z Pruszkowa do Warszawy aha czyli musiałaby pani se taki na trzydzieści dni by kosztował panią czterdzieści sześć osiemdziesiąt czterdzieści sześć osiemdziesiąt to taki bilet bym tak to się nazywa bilet sieciowy imienny bilet sieciowy dziękuję bardzo do widzenia proszę bardzo do widzenia

asr transcript: dzień dobry dzień dobry proszę pana ja mam takie pytanie jestem emerytką i chcę se 

step_type reference_word_pos reference_word_text hypothesis_word_pos  \
0    DELETION               PRON                 xxx                       
1     CORRECT               NOUN               dzień                NOUN   
2     CORRECT                ADJ               dobry                 ADJ   
3     CORRECT               NOUN               dzień                NOUN   
4     CORRECT                ADJ               dobry                 ADJ   
..        ...                ...                 ...                 ...   
143  DELETION               NOUN            widzenia                       
144   CORRECT               VERB              proszę                VERB   
145   CORRECT                ADV              bardzo                 ADV   
146  DELETION                ADP                  do                       
147   CORRECT               NOUN            widzenia                NOUN   

    hypothesis_word_text  
0                         
1                  dzień  
2                  dobry  
3                  dzień  
4                  dobry  
..                   ...  
143                       
144               proszę  
145               bardzo  
146                       
147             widzenia  

[148 rows x 5 columns]

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------
gold transcript: dzień dobry xxx słucham dzień dobry ja się chciałem zapytać o autobus sto dwadzieścia trzy z przystanku Meissnera w kierunku Ronda Wiatraczna dobrze już momencik sto dwadzieścia trzy chwileczkę dobrze przystanek Meissnera kierunek Wiatraczna już panu podaję kiedy pan życzy dzisiaj ? tak teraz proszę bardzo proszę pana to mamy tak dwudziesta zero dziewięć i dwadzieścia dziewięć dobrze dziękuję bardzo dziękuję uprzejmie do widzenia do widzenia

asr transcript: dzień dobry słucham dzień dobry ja się chciałem zapytać o autobus 123 z przystanku meissnera w kierunku ronda wiatraczna dobrze już momencik 100 chwileczkę dobrze przystanek meissnera kierunek wiatraczna już panu podaję kiedy pan życzy dzisiaj tak teraz proszę bardzo proszę pana to mamy tak dwudziesta 0 9 i 29 dobrze dziękuję bar

step_type reference_word_pos reference_word_text hypothesis_word_pos  \
0    CORRECT               NOUN               dzień                NOUN   
1    CORRECT                ADJ               dobry                 ADJ   
2   DELETION               NOUN                 xxx                       
3    CORRECT               VERB             słucham                VERB   
4    CORRECT               NOUN               dzień                NOUN   
..       ...                ...                 ...                 ...   
61   CORRECT                ADV           uprzejmie                 ADV   
62   CORRECT                ADP                  do                 ADP   
63   CORRECT               NOUN            widzenia                NOUN   
64   CORRECT                ADP                  do                 ADP   
65   CORRECT               NOUN            widzenia                NOUN   

   hypothesis_word_text  
0                 dzień  
1                 dobry  
2                        
3               słucham  
4                 dzień  
..                  ...  
61            uprzejmie  
62                   do  
63             widzenia  
64                   do  
65             widzenia  

[66 rows x 5 columns]

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------
gold transcript: dobry wieczór xxx słucham dzień dobry ja mam takie pytanie bo dowiedziałam się właśnie jestem w sumie doktorantką że obowiązuje mnie czterdziestoośmioprocentowa zniżka na MZK i teraz mam takie pytanie bo ja właściwie ukończyłam studia doktoranckie dostanę świadectwo ukończenia tych studiów ale praktycznie zostało mi pisanie pracy doktorskiej i teraz mi już legitymacji nie podbijają czy dalej mogę korzystać z tej zniżki ? znaczy proszę pani ta zniżka przysługuje uczestnikom studiów doktoranckich ona przysługuje właśnie na podstawie legitymacji jeśli nie ma pani legitymacji to niestety czyli jeżeli mam po prostu nie podbijaną bo już studia ukończyłam ale jeszcze piszę pracę doktorską to już chyba raczej nie to już nie przysługuje niestety aha no to dziękuję ślicznie do widzenia bardzo 

...

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------
gold transcript: xxx dzień dobry dzień dobry proszę pana ja potrzebuję dojechać z przystanku Młodzieńcza tak z Ronda Waszyngtona może pan mi podać podać jak mogę dojechać od przystanku Młodzieńcza ? tak do trzeba od Młodzieńczej wsiąść albo sto dziewięćdziesiąt pięćset dwanaście siedemset osiemnaście dojechać do Dworca Wileńskiego do Wileńskiego tak ? tak i z Wileńskiego najlepiej w tramwaj dwadzieścia pięć ewentualnie autobus sto jeden z pięćset dziewięć a czy z Wileńskiego już tramwajem tak ? tak tramwaj dwadzieścia pięć dwadzieścia pięć tak ? tak dobrze dziękuję bardzo proszę bardzo a proszę pana może pan mi jeszcze powiedzieć czy ulica Francuska jest w tych okolicach ? jeszcze raz pan powtórzy ? ulica Francuska ona odchodzi od Ronda Waszyngtona odchodzi tak ? tak a Francuska pięćdziesiąt to jest 

step_type reference_word_pos reference_word_text hypothesis_word_pos  \
0    DELETION               PRON                 xxx                       
1     CORRECT               NOUN               dzień                NOUN   
2     CORRECT                ADJ               dobry                 ADJ   
3     CORRECT               NOUN               dzień                NOUN   
4     CORRECT                ADJ               dobry                 ADJ   
..        ...                ...                 ...                 ...   
141   CORRECT               VERB            dziękuję                VERB   
142   CORRECT                ADV              bardzo                 ADV   
143  DELETION               VERB              proszę                       
144   CORRECT                ADP                  do                 ADP   
145   CORRECT               NOUN            widzenia                NOUN   

    hypothesis_word_text  
0                         
1                  dzień  
2                  dobry  
3                  dzień  
4                  dobry  
..                   ...  
141             dziękuję  
142               bardzo  
143                       
144                   do  
145             widzenia  

[146 rows x 5 columns]

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------
gold transcript: dzień dobry xxx w czym mogę pomóc ? dzień dobry proszę pana chciałam uzyskać od pana taką informację proszę mi powiedzieć że chodzi mi o ulgi chodzi mi o ulgi czy jeżeli dziecko ma bezpłatne przejazdy autobusowe i tramwajowe czy na tą szybką emzetkę dziecko też ma musi płacić bilet ? to znaczy na Szybką Kolej Miejską ? tak nie proszę panią te i te bezpłatne przejazdy również przysługują i na ten środek transportu aha dobrze dobrze bo wie pan bo dziecko ma po prostu bezpłatnie jeździ autobusami i tramwajami ja jestem jako jego opiekun po prostu chciałam się tylko dowiedzieć czy przysługuje nam taka ulga jeżeli dziecko ma taką legitymację i po prostu czy dziecko będzie może czy dziecko może jeździć na tą szybką kolej na tą legitymację tak ? tak proszę panią ze względu na to że na Szybk

step_type reference_word_pos reference_word_text hypothesis_word_pos  \
0         CORRECT               NOUN               dzień                NOUN   
1         CORRECT                ADJ               dobry                 ADJ   
2        DELETION                  X                 xxx                       
3         CORRECT                ADP                   w                 ADP   
4         CORRECT               PRON                czym                PRON   
..            ...                ...                 ...                 ...   
207  SUBSTITUTION               NOUN            widzenia                 AUX   
208  SUBSTITUTION               VERB            dziękuję                PRON   
209       CORRECT                ADV           wzajemnie                 ADV   
210       CORRECT                ADP                  do                 ADP   
211       CORRECT               NOUN            widzenia                NOUN   

    hypothesis_word_text  
0                  dzień  
1                  dobry  
2                         
3                      w  
4                   czym  
..                   ...  
207                   to  
208                   ja  
209            wzajemnie  
210                   do  
211             widzenia  

[212 rows x 5 columns]

--------------------------------------------------------------
--------------------------------------------------------------
--------------------------------------------------------------
